In [ ]:
! pip install transformers
! pip3 install datasets
! pip install accelerate

huggingface/tokenizers: The current process just got forked, after parallelism has already been used. Disabling parallelism to avoid deadlocks...
To disable this warning, you can either:
	- Avoid using `tokenizers` before the fork if possible
	- Explicitly set the environment variable TOKENIZERS_PARALLELISM=(true | false)



[notice] A new release of pip is available: 23.1.2 -> 23.3.1
[notice] To update, run: pip install --upgrade pip


huggingface/tokenizers: The current process just got forked, after parallelism has already been used. Disabling parallelism to avoid deadlocks...
To disable this warning, you can either:
	- Avoid using `tokenizers` before the fork if possible
	- Explicitly set the environment variable TOKENIZERS_PARALLELISM=(true | false)



[notice] A new release of pip is available: 23.1.2 -> 23.3.1
[notice] To update, run: pip install --upgrade pip


huggingface/tokenizers: The current process just got forked, after parallelism has already been used. Disabling parallelism to avoid deadlocks...
To disable this warning, you can either:
	- Avoid using `tokenizers` before the fork if possible
	- Explicitly set the environment variable TOKENIZERS_PARALLELISM=(true | false)



[notice] A new release of pip is available: 23.1.2 -> 23.3.1
[notice] To update, run: pip install --upgrade pip


In [ ]:
! pip install accelerate -U

huggingface/tokenizers: The current process just got forked, after parallelism has already been used. Disabling parallelism to avoid deadlocks...
To disable this warning, you can either:
	- Avoid using `tokenizers` before the fork if possible
	- Explicitly set the environment variable TOKENIZERS_PARALLELISM=(true | false)



[notice] A new release of pip is available: 23.1.2 -> 23.3.1
[notice] To update, run: pip install --upgrade pip


In [ ]:
! pip install torchvision
! pip install tqdm

huggingface/tokenizers: The current process just got forked, after parallelism has already been used. Disabling parallelism to avoid deadlocks...
To disable this warning, you can either:
	- Avoid using `tokenizers` before the fork if possible
	- Explicitly set the environment variable TOKENIZERS_PARALLELISM=(true | false)



[notice] A new release of pip is available: 23.1.2 -> 23.3.1
[notice] To update, run: pip install --upgrade pip


huggingface/tokenizers: The current process just got forked, after parallelism has already been used. Disabling parallelism to avoid deadlocks...
To disable this warning, you can either:
	- Avoid using `tokenizers` before the fork if possible
	- Explicitly set the environment variable TOKENIZERS_PARALLELISM=(true | false)



[notice] A new release of pip is available: 23.1.2 -> 23.3.1
[notice] To update, run: pip install --upgrade pip


In [ ]:
import torch
import torch.nn as nn
import torch.nn.functional as F
import torch.optim as optim
from torch.utils.data import Dataset, DataLoader
from torchvision import transforms

import numpy as np
import pandas as pd
import random
import pickle
import matplotlib.pyplot as plt
from datasets import load_dataset
from tqdm import tqdm

device = torch.device('cuda' if torch.cuda.is_available() else 'cpu')

In [ ]:
from s3fs import S3FileSystem
s3 = S3FileSystem()

In [ ]:
class AroGOTDataset(Dataset):
    def __init__(self, aro_path, dependency_graph_path, s3=None, coco=None, ):
        self.s3 = s3
        self.coco = self._load_coco(coco)
        self.aro = self._load_aro(aro_path)
        self.dependency_graphs = self._load_dependency_graph(dependency_graph_path)
        self.aro_graph = self._prepare_aro_graphs()

        file_df = self._build_file_directory()
        self.full_df = self.aro_graph.merge(file_df, how="inner", left_on="filename", right_on="file_name")

    def __len__(self):
        return len(self.aro_graph)

    def __getitem__(self, idx):
        row = self.full_df.loc[idx]
        coco_split, coco_index = row["split"], int(row["coco_id"])

        image = self.coco[coco_split][coco_index]["image"]
        caption = row["caption"]
        label = row["label"]

        adj_matrix = torch.Tensor(row["adj_matrix"])

        return caption, image.convert("RGB"), adj_matrix, label

    def _prepare_aro_graphs(self):
        captions_with_graphs = self.aro.merge(self.dependency_graphs, "left", left_on="title", right_on="caption")
        captions_with_graphs = captions_with_graphs[~captions_with_graphs["caption"].isnull()]
        captions_with_graphs["filename"] = captions_with_graphs["filepath"].apply(lambda s: s.split("/")[-1])
        captions_with_graphs = captions_with_graphs[~captions_with_graphs["adj_matrix"].isnull()]
        return captions_with_graphs

    def _load_coco(self, coco=None):
        print("-----Loading COCO-----")
        if coco is not None:
            return coco

        return load_dataset(
              "shunk031/MSCOCO",
              year=2014,
              coco_task="captions",
              cache_dir="cache/coco"
          )

    def _load_aro(self, path):
        print("-----Loading ARO-----")
        aro = pd.read_csv(path, sep="\t").drop(columns="Unnamed: 0")
        aro["negative_captions"] = aro.apply(lambda row: self._extract_captions([row["neg_caption"]]), axis=1)
        aro["title"] = aro.apply(lambda row: row["title"].strip().replace("  ", " ").replace(" .", "."), axis=1)

        positive_captions = aro[["title", "filepath"]]
        positive_captions["label"] = 1

        negative_captions = aro[["negative_captions", "filepath"]].rename(columns={"negative_captions": "title"})
        negative_captions["label"] = 0

        all_captions_aro = pd.concat([
            positive_captions,
            negative_captions
        ])

        return all_captions_aro

    def _load_dependency_graph(self, path):
        print("-----Loading Dependency Graphs-----")
        if self.s3 is not None:
            with self.s3.open(path, 'rb') as f:
              data = pickle.load(f)
        else:
            with open(path, 'rb') as f:
              data = pickle.load(f)

        dependency_graphs = pd.DataFrame(data).T.reset_index().rename(
          columns={
              "index": "caption",
              0: "adj_matrix",
              1: "edge_types",
              2: "tokenized"
            }
        )
        dependency_graphs = dependency_graphs[dependency_graphs["adj_matrix"].apply(lambda s: not isinstance(s, float))]
        dependency_graphs["caption"] = dependency_graphs.apply(lambda row: row["caption"].strip().replace("  ", " ").replace(" .", "."), axis=1)
        return dependency_graphs

    def _build_file_directory(self):
        file_dfs = []
        for split in ("train", "validation"):
            files = pd.DataFrame.from_dict({
                "file_name": self.coco[split]["file_name"],
                "coco_id": np.arange(len(self.coco[split]["file_name"]))
              }
            )
            files["split"] = split
            file_dfs.append(files)

        return pd.concat(file_dfs)

    def _polish_caption(self, s):
        return s.replace('"', "").replace("  ", " ").replace(" .", ".").strip().strip("[]'")

    def _extract_captions(self, captions):
        if len(captions) > 1:
            raise Exception("Unexpected length")
        return random.choice([self._polish_caption(s) for s in captions[0].split("',")])

In [ ]:
! pip install pycocotools

huggingface/tokenizers: The current process just got forked, after parallelism has already been used. Disabling parallelism to avoid deadlocks...
To disable this warning, you can either:
	- Avoid using `tokenizers` before the fork if possible
	- Explicitly set the environment variable TOKENIZERS_PARALLELISM=(true | false)



[notice] A new release of pip is available: 23.1.2 -> 23.3.1
[notice] To update, run: pip install --upgrade pip


In [ ]:
aro_got_train_dataset = AroGOTDataset(aro_path="s3://ebotta-storage/train_neg_clip.tsv", dependency_graph_path='s3://ebotta-storage/aro_graphs.pkl', s3=s3)
aro_got_val_dataset = AroGOTDataset(aro_path="s3://ebotta-storage/valid_neg_clip.tsv", dependency_graph_path='s3://ebotta-storage/aro_graphs.pkl', s3=s3, coco=aro_got_train_dataset.coco)

-----Loading COCO-----
-----Loading ARO-----


/tmp/ipykernel_1933/1063286789.py:53: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  positive_captions["label"] = 1


-----Loading Dependency Graphs-----
-----Loading COCO-----
-----Loading ARO-----


/tmp/ipykernel_1933/1063286789.py:53: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  positive_captions["label"] = 1


-----Loading Dependency Graphs-----


In [ ]:
from torch.utils.data import dataloader

def data_collator(batch):
    captions = [element[0] for element in batch]
    images = [element[1] for element in batch]

    adj_graphs = torch.zeros(len(batch), 77, 77).detach()
    for i, element in enumerate(batch):
        ax1, ax2 = element[2].shape
        adj_graphs[i, :ax1, :ax2] = element[2]

    labels = torch.Tensor([element[3] for element in batch]).detach()
    return captions, images, adj_graphs, labels

train_dataloader = DataLoader(aro_got_train_dataset, batch_size=16, collate_fn=data_collator, shuffle=True)
val_dataloader = DataLoader(aro_got_val_dataset, batch_size=16, collate_fn=data_collator)

In [ ]:
aro_got_train_dataset.full_df

title   
0       A woman marking a cake with the back of a chef...  \
1       A back marking a cake with the woman of a chef...   
2        a young kid with head phones on using a computer   
3        a head kid with young phones on using a computer   
4       A small child wearing headphones plays on the ...   
...                                                   ...   
215969  I ca nt tell whether its coming into night or ...   
215970  A wall with a sidewalk next to it there s also...   
215971  I can not see the kite that is flying the pers...   
215972  A unattended decker bus that s sitting in the ...   
215973    A clock standing next to a woman that s lit up.   

                                              filepath  label   
0           coco/val2014/COCO_val2014_000000522418.jpg      1  \
1           coco/val2014/COCO_val2014_000000522418.jpg      0   
2           coco/val2014/COCO_val2014_000000318219.jpg      1   
3           coco/val2014/COCO_val2014_000000318219.jpg      0   
4           coco/val2014/COCO_val2014_000000554625.jpg      1   
...                                                ...    ...   
215969  coco/train2014/COCO_train2014_000000414022.jpg      0   
215970  coco/train2014/COCO_train2014_000000143436.jpg      0   
215971  coco/train2014/COCO_train2014_000000458135.jpg      0   
215972  coco/train2014/COCO_train2014_000000462057.jpg      0   
215973  coco/train2014/COCO_train2014_000000268940.jpg      0   

                                                  caption   
0       A woman marking a cake with the back of a chef...  \
1       A back marking a cake with the woman of a chef...   
2        a young kid with head phones on using a computer   
3        a head kid with young phones on using a computer   
4       A small child wearing headphones plays on the ...   
...                                                   ...   
215969  I ca nt tell whether its coming into night or ...   
215970  A wall with a sidewalk next to it there s also...   
215971  I can not see the kite that is flying the pers...   
215972  A unattended decker bus that s sitting in the ...   
215973    A clock standing next to a woman that s lit up.   

                                               adj_matrix   
0       [[0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0,...  \
1       [[0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0,...   
2       [[0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0], [0, 0, ...   
3       [[0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0], [0, 0, ...   
4       [[0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0], [0, ...   
...                                                   ...   
215969  [[0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0,...   
215970  [[0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0,...   
215971  [[0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0,...   
215972  [[0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0,...   
215973  [[0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0], [...   

                                               edge_types   
0       [[None, None, None, None, None, None, None, No...  \
1       [[None, None, None, None, None, None, None, No...   
2       [[None, None, None, None, None, None, None, No...   
3       [[None, None, None, None, None, None, None, No...   
4       [[None, None, None, None, None, None, None, No...   
...                                                   ...   
215969  [[None, None, None, None, None, None, None, No...   
215970  [[None, None, None, None, None, None, None, No...   
215971  [[None, None, None, None, None, None, None, No...   
215972  [[None, None, None, None, None, None, None, No...   
215973  [[None, None, None, None, None, None, None, No...   

                                                tokenized   
0       [[CLS], a, woman, marking, a, cake, with, the,...  \
1       [[CLS], a, back, marking, a, cake, with, the, ...   
2       [[CLS], a, young, kid, with, head, phones, on,...   
3       [[CLS], a, head, kid, with, young, phones, on,...   
4       [[CLS], a, small, child, w

In [ ]:
aro_got_val_dataset.full_df

title   
0     A child holding a flowered umbrella and pettin...  \
1     A umbrella holding a flowered child and pettin...   
2     A narrow kitchen filled with appliances and co...   
3     A narrow cooking filled with appliances and ki...   
4     A little girl holding a kitten next to a blue ...   
...                                                 ...   
9531  Two women are standing on a court tennis holdi...   
9532        A person and a kid on top of a refrigerator   
9533        A person and a refrigerator on top of a kid   
9534  A brown teddy bear wearing a Hawaiian shirt ne...   
9535  a hawaiian shirt bear wearing a brown teddy ne...   

                                        filepath  label   
0     coco/val2014/COCO_val2014_000000184613.jpg      1  \
1     coco/val2014/COCO_val2014_000000184613.jpg      0   
2     coco/val2014/COCO_val2014_000000403013.jpg      1   
3     coco/val2014/COCO_val2014_000000403013.jpg      0   
4     coco/val2014/COCO_val2014_000000562150.jpg      1   
...                                          ...    ...   
9531  coco/val2014/COCO_val2014_000000451949.jpg      0   
9532  coco/val2014/COCO_val2014_000000203138.jpg      1   
9533  coco/val2014/COCO_val2014_000000203138.jpg      0   
9534  coco/val2014/COCO_val2014_000000296759.jpg      1   
9535  coco/val2014/COCO_val2014_000000296759.jpg      0   

                                                caption   
0     A child holding a flowered umbrella and pettin...  \
1     A umbrella holding a flowered child and pettin...   
2     A narrow kitchen filled with appliances and co...   
3     A narrow cooking filled with appliances and ki...   
4     A little girl holding a kitten next to a blue ...   
...                                                 ...   
9531  Two women are standing on a court tennis holdi...   
9532        A person and a kid on top of a refrigerator   
9533        A person and a refrigerator on top of a kid   
9534  A brown teddy bear wearing a Hawaiian shirt ne...   
9535  a hawaiian shirt bear wearing a brown teddy ne...   

                                             adj_matrix   
0     [[0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0,...  \
1     [[0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0,...   
2     [[0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0], [...   
3     [[0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0], [...   
4     [[0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0], [...   
...                                                 ...   
9531  [[0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0], [...   
9532  [[0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0], [0, 0, ...   
9533  [[0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0], [0, 0, ...   
9534  [[0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0,...   
9535  [[0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0,...   

                                             edge_types   
0     [[None, None, None, None, None, None, None, No...  \
1     [[None, None, None, None, None, None, None, No...   
2     [[None, None, None, None, None, None, None, No...   
3     [[None, None, None, None, None, None, None, No...   
4     [[None, None, None, None, None, None, None, No...   
...                                                 ...   
9531  [[None, None, None, None, None, None, None, No...   
9532  [[None, None, None, None, None, None, None, No...   
9533  [[None, None, None, None, None, None, None, No...   
9534  [[None, None, None, None, None, None, None, No...   
9535  [[None, None, None, None, None, None, None, No...   

                                              tokenized   
0     [[CLS], a, child, holding, a, flower, ##ed, um...  \
1     [[CLS], a, umbrella, holding, a, flower, ##ed,...   
2     [[CLS], a, narrow, kitchen, filled, with, appl...   
3     [[CLS], a, narrow, cooking, filled, with, appl...   
4     [[CLS], a, little, girl, holding, a, kitten, n...   
...                                                 ...   
9531  [[CLS], two, women, are, standing, on, a, cour...   
9532  [[CLS], a, person, and, a, 

In [ ]:
        if image_masked_embeddings is not None or multimodal_masked_embeddings is not None:
            if mim_labels is None and return_loss:
                if self.image_codebook is None:
                    raise RuntimeError(
                        "`return_loss` is set to True but the image codebook is not initialized and no `mim_labels` "
                        " have been passed. Reinstantiate the model with `init_codebook` set to True or "
                        "pass in your custom `mim_labels`"
                    )
                if codebook_pixel_values is None:
                    raise ValueError(
                        "`codebook_pixel_value` are required to generate `mim_labels` if loss is expected. "
                        "Call `AutoProcessor` with `return_codebook_pixels` set to True"
                    )
                mim_labels = self.image_codebook.get_codebook_indices(codebook_pixel_values)
        # Unimodal MIM Loss
        # If multimodal embeddings are present, we will calculate MMM loss
        if self.mim_weight > 0 and image_masked_embeddings is not None and multimodal_masked_embeddings is None:
            sequence_for_image = image_masked_embeddings

            if mim_labels is not None:
                mim_labels = self._resize_to_2d(mim_labels)
                bool_masked_pos = self._resize_to_2d(bool_masked_pos)
                mim_labels[bool_masked_pos.ne(True)] = self.ce_ignore_index

                sequence_for_image = sequence_for_image[:, -mim_labels.size(1) :, :]
                masked_tokens = mim_labels.ne(self.ce_ignore_index)
                mim_labels_filtered = mim_labels[masked_tokens]
                sequence_for_image = sequence_for_image[masked_tokens, :]
                mim_logits = self.mim_head(sequence_for_image)
                if return_loss:
                    mim_loss = nn.functional.cross_entropy(
                        mim_logits.view(-1, self.image_vocab_size), mim_labels_filtered.view(-1)
                    )
                    mim_loss *= self.mim_weight
            else:
                mim_logits = self.mim_head(sequence_for_image)

        # Unimodal MLM Loss
        if self.mlm_weight > 0 and text_masked_embeddings is not None and multimodal_masked_embeddings is None:
            sequence_for_text = text_masked_embeddings
            if mlm_labels is not None:
                mlm_labels = self._resize_to_2d(mlm_labels)
                sequence_for_text = sequence_for_text[:, -mlm_labels.size(1) :, :]
                masked_tokens = mlm_labels.ne(self.ce_ignore_index)
                mlm_labels_filtered = mlm_labels[masked_tokens]
                sequence_for_text = sequence_for_text[masked_tokens, :]
                mlm_logits = self.mlm_head(sequence_for_text)
                if return_loss:
                    mlm_loss = nn.functional.cross_entropy(
                        mlm_logits.view(-1, self.text_vocab_size), mlm_labels_filtered.view(-1)
                    )
                    mlm_loss *= self.mlm_weight
            else:
                mlm_logits = self.mlm_head(sequence_for_text)


NameError: name 'image_masked_embeddings' is not defined

In [ ]:
from transformers import FlavaProcessor, FlavaForPreTraining, FlavaModel

import collections
import math
from collections import OrderedDict
from dataclasses import dataclass
from typing import Any, Dict, List, Optional, Set, Tuple, Union

import torch
import torch.utils.checkpoint
from torch import nn
import pdb

from transformers.activations import ACT2FN
from transformers.modeling_outputs import BaseModelOutput, BaseModelOutputWithPooling
from transformers.modeling_utils import PreTrainedModel, find_pruneable_heads_and_indices, prune_linear_layer
from transformers.utils import (
    ModelOutput,
    add_code_sample_docstrings,
    add_start_docstrings,
    add_start_docstrings_to_model_forward,
    logging,
    replace_return_docstrings,
)
from transformers.models.flava.configuration_flava import (
    FlavaConfig,
    FlavaImageCodebookConfig,
    FlavaImageConfig,
    FlavaMultimodalConfig,
    FlavaTextConfig,
)
from transformers.models.flava.modeling_flava import (
    FlavaForPreTrainingOutput,
    FlavaLosses,
    FLAVA_PRETRAINED_MODEL_ARCHIVE_LIST,
    FLAVA_CODEBOOK_PRETRAINED_MODEL_ARCHIVE_LIST,
    LOGIT_SCALE_CLAMP_MIN,
    LOGIT_SCALE_CLAMP_MAX,
    FlavaPossibleConfigs,
    logger
)

@dataclass
class FlavaGOTLosses(FlavaLosses):
    got: Optional[torch.FloatTensor] = None
    itm_got_finetuning_loss: Optional[torch.FloatTensor] = None


class FlavaGOTConfig(FlavaConfig):
    def __init__(self, got_weight=1.0, *args, **kwargs):
        super().__init__(*args, **kwargs)

        self.got_weight = got_weight

@dataclass
class FlavaGOTForPreTrainingOutput(FlavaForPreTrainingOutput):
    loss_info: Optional[FlavaGOTLosses] = None


class FlavaGOTForPreTraining(FlavaForPreTraining):
    def __init__(self, *args, **kwargs):
        super().__init__(*args, **kwargs)

        self.got_loss = GOTLoss(got_lambda=0.5)
        self.got_weight = 1.0

    def forward(
        self,
        input_ids: Optional[torch.LongTensor] = None,
        input_ids_masked: Optional[torch.LongTensor] = None,
        pixel_values: Optional[torch.FloatTensor] = None,
        codebook_pixel_values: Optional[torch.FloatTensor] = None,
        attention_mask: Optional[torch.Tensor] = None,
        token_type_ids: Optional[torch.Tensor] = None,
        bool_masked_pos: Optional[torch.Tensor] = None,
        position_ids: Optional[torch.LongTensor] = None,
        image_attention_mask: Optional[torch.Tensor] = None,
        skip_unmasked_multimodal_encoder: bool = None,
        mlm_labels: Optional[torch.Tensor] = None,
        mim_labels: Optional[torch.Tensor] = None,
        itm_labels: Optional[torch.Tensor] = None,
        output_attentions: Optional[bool] = None,
        output_hidden_states: bool = True,
        return_dict: Optional[bool] = None,
        return_loss: Optional[bool] = None,
        text_dependency_graph = None,
    ) -> Union[Tuple[torch.Tensor], FlavaGOTForPreTrainingOutput]:
        """
        Examples:
        ```python
        >>> from PIL import Image
        >>> import requests
        >>> from transformers import FlavaForPreTraining, AutoProcessor

        >>> url = "http://images.cocodataset.org/val2017/000000039769.jpg"
        >>> image = Image.open(requests.get(url, stream=True).raw)

        >>> model = FlavaForPreTraining.from_pretrained("facebook/flava-full")
        >>> processor = AutoProcessor.from_pretrained("facebook/flava-full")

        >>> text = ["a photo of a cat"]

        >>> inputs = processor(
        ...     images=[image],
        ...     text=text,
        ...     return_masks=True,
        ...     return_codebook_pixels=True,
        ...     padding=True,
        ...     max_length=77,
        ...     return_tensors="pt",
        ... )


        >>> output = model(**inputs)
        ```

        Return:

        """
        return_dict = return_dict if return_dict is not None else self.config.use_return_dict
        return_loss = return_loss if return_loss is not None else self.config.return_loss

        skip_unmasked_multimodal_encoder = (
            skip_unmasked_multimodal_encoder
            if skip_unmasked_multimodal_encoder is not None
            else self.skip_unmasked_multimodal_encoder
        )

        if input_ids_masked is None and input_ids is not None:
            logger.warning(
                "`input_ids_masked` isn't passed which means MLM loss won't be calculated correctlySetting it to"
                " `input_ids` so that model can work. Please pass it if this is unintentional. This is usually OKAY if"
                " you are doing inference on unmasked text..."
            )
            input_ids_masked = input_ids

        flava_output = self.flava(
            input_ids=input_ids,
            pixel_values=pixel_values,
            attention_mask=attention_mask,
            token_type_ids=token_type_ids,
            position_ids=position_ids,
            image_attention_mask=image_attention_mask,
            # Don't need unmasked multimodal embedding for anything so skip it
            # NOTE: ITM uses masked version
            skip_multimodal_encoder=skip_unmasked_multimodal_encoder,
            output_attentions=output_attentions,
            output_hidden_states=output_hidden_states,
            # Pass true to have deterministic outputs
            return_dict=True,
        )

        flava_masked_output = self.flava(
            input_ids=input_ids_masked,
            pixel_values=pixel_values,
            attention_mask=attention_mask,
            token_type_ids=token_type_ids,
            image_attention_mask=image_attention_mask,
            bool_masked_pos=bool_masked_pos,
            output_attentions=output_attentions,
            output_hidden_states=output_hidden_states,
            return_dict=True,
        )


        pos_mask = None

        image_embeddings = flava_output.image_embeddings
        text_embeddings = flava_output.text_embeddings
        image_masked_embeddings = flava_masked_output.image_embeddings
        text_masked_embeddings = flava_masked_output.text_embeddings
        multimodal_masked_embeddings = flava_masked_output.multimodal_embeddings

        total_loss = mim_loss = mlm_loss = mmm_text_loss = mmm_image_loss = gc_loss = itm_loss = itm_got_finetuning_loss = None
        mim_logits = mlm_logits = mmm_text_logits = mmm_image_logits = None
        itm_logits = logits_per_image = logits_per_text = None

        # Calculate mim_labels if necessary from the image_codebook

        got_loss = self.got_loss.GOT(text_masked_embeddings, image_masked_embeddings, text_dependency_graph)

        # ITM Loss
        if self.itm_weight > 0 and multimodal_masked_embeddings is not None:
            itm_logits = self.itm_head(multimodal_masked_embeddings)

            if itm_labels is not None:
                pos_pairs = itm_labels.ne(0)
                pos_mask = torch.where(pos_pairs.any(), pos_pairs, pos_pairs.new([True]))
                pos_mask = None
                if return_loss:
                    #print(itm_logits, itm_labels)
                    itm_loss = nn.functional.cross_entropy(itm_logits.cuda(), itm_labels.type(torch.LongTensor).cuda())
                    itm_loss *= self.itm_weight

                if multimodal_masked_embeddings is not None:
                    multimodal_masked_embeddings = multimodal_masked_embeddings[pos_mask]

                if mlm_labels is not None:
                    mlm_labels = mlm_labels[pos_mask]

                if mim_labels is not None:
                    mim_labels = mim_labels[pos_mask]

        itm_got_finetuning_loss = self.got_weight*got_loss
        # GOT Regularization Loss (TODO: Integrate GOT code here)

        # MMM Image Loss
        if multimodal_masked_embeddings is not None and self.mmm_image_weight > 0:
            sequence_for_image = multimodal_masked_embeddings
            end_index = image_masked_embeddings.size(1) - 1
            sequence_for_image = sequence_for_image[:, 2 : 2 + end_index, :]

            if pos_mask is not None:
                sequence_for_image = sequence_for_image[pos_mask]
            if mim_labels is not None:
                mim_labels = self._resize_to_2d(mim_labels)
                bool_masked_pos = self._resize_to_2d(bool_masked_pos)
                mim_labels[bool_masked_pos.ne(True)] = self.ce_ignore_index

                masked_tokens = mim_labels.ne(self.ce_ignore_index)
                mim_labels_filtered = mim_labels[masked_tokens]
                sequence_for_image = sequence_for_image[masked_tokens, :]
                mmm_image_logits = self.mmm_image_head(sequence_for_image)
                if return_loss:
                    mmm_image_loss = nn.functional.cross_entropy(
                        mmm_image_logits.view(-1, self.image_vocab_size), mim_labels_filtered.view(-1)
                    )
                    mmm_image_loss *= self.mmm_image_weight
            else:
                mmm_image_logits = self.mmm_image_head(sequence_for_image)

        # MMM Text Loss
        if multimodal_masked_embeddings is not None and self.mmm_text_weight > 0:
            sequence_for_text = multimodal_masked_embeddings
            sequence_for_text = sequence_for_text[:, -text_masked_embeddings.size(1) :, :]
            if pos_mask is not None:
                sequence_for_text = sequence_for_text[pos_mask]

            if mlm_labels is not None:
                mlm_labels = self._resize_to_2d(mlm_labels)
                masked_tokens = mlm_labels.ne(self.ce_ignore_index)
                mlm_labels_filtered = mlm_labels[masked_tokens]
                sequence_for_text = sequence_for_text[masked_tokens, :]
                mmm_text_logits = self.mmm_text_head(sequence_for_text)
                if return_loss:
                    mmm_text_loss = nn.functional.cross_entropy(
                        mmm_text_logits.view(-1, self.text_vocab_size), mlm_labels_filtered.view(-1)
                    )
                    mmm_text_loss *= self.mmm_text_weight
            else:
                mmm_text_logits = self.mmm_text_head(sequence_for_text)

        # Global Contrastive Loss
        if image_embeddings is not None and text_embeddings is not None and self.global_contrastive_weight > 0:
            text_embedding = self.flava.text_projection(text_embeddings[:, 0, :])
            text_embedding = nn.functional.normalize(text_embedding, dim=-1)

            image_embedding = self.flava.image_projection(image_embeddings[:, 0, :])
            image_embedding = nn.functional.normalize(image_embedding, dim=-1)

            self.flava.logit_scale.data.clamp_(LOGIT_SCALE_CLAMP_MIN, LOGIT_SCALE_CLAMP_MAX)

            logits_per_image, logits_per_text, gc_labels = self.global_contrastive_head(
                image_embedding, text_embedding, self.flava.logit_scale
            )

            # Apply ITM negative mask if any
            #if pos_mask is not None:
            #    logits_per_image = logits_per_image[pos_mask]
            #    logits_per_text = logits_per_text[pos_mask]
            #    gc_labels = gc_labels[pos_mask]

            if return_loss:
                gc_loss_image = nn.functional.cross_entropy(logits_per_image, gc_labels)
                gc_loss_text = nn.functional.cross_entropy(logits_per_text, gc_labels)
                gc_loss = (gc_loss_image + gc_loss_text) / 2
                gc_loss *= self.global_contrastive_weight

        flava_losses = FlavaGOTLosses(
            itm_got_finetuning_loss=itm_got_finetuning_loss,
            got=got_loss,
            mim=mim_loss,
            mlm=mlm_loss,
            itm=itm_loss,
            global_contrastive=gc_loss,
            mmm_image=mmm_image_loss,
            mmm_text=mmm_text_loss,
        )

        if return_loss and not flava_losses.all_none():
            total_loss = sum(loss if loss is not None else 0 for loss in flava_losses.values())

        if not return_dict:
            output = (
                image_embeddings,
                flava_output.image_output.to_tuple() if flava_output.image_output is not None else None,
                text_embeddings,
                flava_output.text_output.to_tuple() if flava_output.text_output is not None else None,
                flava_output.multimodal_embeddings,
                flava_output.multimodal_output.to_tuple() if flava_output.multimodal_output is not None else None,
                image_masked_embeddings,
                flava_masked_output.image_output.to_tuple() if flava_masked_output.image_output is not None else None,
                text_masked_embeddings,
                flava_masked_output.text_output.to_tuple() if flava_masked_output.text_output is not None else None,
                multimodal_masked_embeddings,
                flava_masked_output.multimodal_output.to_tuple()
                if flava_masked_output.multimodal_output is not None
                else None,
                mim_logits,
                mlm_logits,
                itm_logits,
                logits_per_image,
                logits_per_image,
                mmm_image_logits,
                mmm_text_logits,
            )
            if return_loss and not flava_losses.all_none():
                output = (
                    total_loss,
                    flava_losses,
                ) + output

            # Filter None as transformer by default won't handle it
            return tuple(x for x in output if x is None)

        total_loss = itm_loss + gc_loss + itm_got_finetuning_loss

        return FlavaGOTForPreTrainingOutput(
            loss=total_loss,
            loss_info=flava_losses,
            image_embeddings=image_embeddings,
            image_output=flava_output.image_output,
            text_embeddings=text_embeddings,
            text_output=flava_output.text_output,
            multimodal_embeddings=flava_output.multimodal_embeddings,
            multimodal_output=flava_output.multimodal_output,
            image_masked_embeddings=image_masked_embeddings,
            image_masked_output=flava_masked_output.image_output,
            text_masked_embeddings=text_masked_embeddings,
            text_masked_output=flava_masked_output.text_output,
            multimodal_masked_embeddings=multimodal_masked_embeddings,
            multimodal_masked_output=flava_masked_output.multimodal_output,
            mim_logits=mim_logits,
            mlm_logits=mlm_logits,
            itm_logits=itm_logits,
            contrastive_logits_per_image=logits_per_image,
            contrastive_logits_per_text=logits_per_text,
            mmm_image_logits=mmm_image_logits,
            mmm_text_logits=mmm_text_logits,
        )

In [ ]:
import numpy as np
import torch
from functools import partial
from sklearn.metrics.pairwise import euclidean_distances
from torch.autograd import Variable
import pdb

def cost_matrix_torch(x, y):
	"Returns the cosine distance"
	# x is the image embedding
	# y is the text embedding
	D = x.size(0)
	x = x.view(D, -1)
	assert(x.size(0)==y.size(0))
	x = x.div(torch.norm(x, p=2, dim=0, keepdim=True) + 1e-12)
	y = y.div(torch.norm(y, p=2, dim=0, keepdim=True) + 1e-12)
	cos_dis = torch.mm(torch.transpose(y,0,1), x)#.t()
	cos_dis = 1 - cos_dis # to minimize this value
	return cos_dis

def IPOT_torch(C, n, m, miu, nu, beta=0.5):
	# C is the distance matrix
	# c: n by m
	# miu: bs * n
	sigma = torch.ones(int(m), 1).float().cuda()/m # bs * m * 1
	T = torch.ones(n, m).cuda()
	C = torch.exp(-C/beta).float()
	for t in range(20):
		T = C * T # n * m
		for k in range(1):
			delta = miu / torch.squeeze(torch.matmul(T, sigma))
			# a = torch.matmul(torch.transpose(T,0,1), torch.unsqueeze(delta,1))
			# sigma = torch.unsqueeze(nu,1) / a
			sigma = torch.unsqueeze(nu,1) / torch.matmul(torch.transpose(T,0,1), torch.unsqueeze(delta,1))
		# tmp = torch.mm(torch.diag(torch.squeeze(delta)), Q)
		# tmp = torch.unsqueeze(delta,1) * A
		# dim_ = torch.diag(torch.squeeze(sigma)).dim()
		# dim_ = torch.diag(torch.squeeze(sigma)).dim()
		# assert (dim_ == 2 or dim_ == 1, "dim_ is %d" % dim_)
		# T = torch.mm(torch.unsqueeze(delta,1) * T, torch.diag(torch.squeeze(sigma)))
		T = torch.unsqueeze(delta,1) * T * sigma.transpose(1,0)
	return T.detach()

def IPOT_distance_torch(C, n, m, miu, nu):
	C = C.float().cuda()
	T = IPOT_torch(C, n, m, miu, nu)
	distance = torch.trace(torch.mm(torch.transpose(C,0,1), T))
	return -distance


def IPOT_distance_torch_batch(C, n, m, miu, nu, iteration):
	# C as a 2 d matrix
	C = C.float().cuda()
	bs = miu.size(0)
	# if C.dim()==2:
	# 	C=C.repeat(bs, 1, 1)
	if C.dim()==2:
		C = torch.unsqueeze(C, 0)
	# if not bs == C.size(0):
	# 	print('break')
	# assert(bs == C.size(0))
	T = IPOT_torch_batch(C, bs, n, m, miu, nu, iteration)
	temp = torch.matmul(torch.transpose(C,1,2), T)
	distance = batch_trace(temp, m, bs)
	return -distance


def IPOT_torch_batch(C, bs, n, m, miu, nu, iteration=20, beta=0.5):
	# C is the distance matrix, 2d matrix
	# c: n by m
	# miu: bs * n
	sigma = torch.ones(bs, int(m), 1).cuda().detach()/float(m) # bs * m * 1
	Q = torch.ones(bs, n, m).cuda().detach().float()
	C = torch.exp(-C/beta)#.unsqueeze(0)
	if nu.dim() < 3:
		nu = torch.unsqueeze(nu,2)
	# if miu.dim()<3:
	# 	miu = torch.unsqueeze(miu,1)
	miu = torch.squeeze(miu)
	for t in range(iteration):
		Q = C * Q # bs * n * m
		for k in range(1):
			delta = torch.unsqueeze((miu / torch.squeeze(torch.bmm(Q, sigma)+1e-6)),2)
			# delta = ((miu / (torch.bmm(Q, sigma) + 1e-6)))
			a = torch.bmm(torch.transpose(Q,1,2), delta)+1e-6
			sigma = nu / a
		Q = delta * Q * sigma.transpose(2,1)
		# Q = torch.matmul(tmp, diag_sigma)
	return Q.detach()

def IPOT_torch_uniform(C, n, m, beta=0.5):
	# C is the distance matrix
	sigma = torch.ones(int(m), 1).cuda()/m
	T = torch.ones(n, m).cuda()
	A = torch.exp(-C/beta)
	for t in range(50):
		Q = A * T # n * m
		for k in range(1):
			delta = 1 / (n * torch.mm(Q, sigma))
			a = torch.mm(torch.transpose(Q,0,1), delta)
			sigma = 1 / (float(m) * a)
		tmp = torch.mm(torch.diag(torch.squeeze(delta)), Q)
		dim_ = torch.diag(torch.squeeze(sigma)).dim()
		assert (dim_ == 2 or dim_ == 1)
		T = torch.mm(tmp, torch.diag(torch.squeeze(sigma)))
	return T.detach()

def IPOT_distance_torch_uniform(C, n, m):
	C = C.float().cuda()
	T = IPOT_torch_uniform(C, n, m)
	distance = torch.trace(torch.mm(torch.transpose(C,0,1), T))
	return distance


def cost_matrix_batch_torch(x, y):
	"Returns the cosine distance batchwise"
	# x is the image feature: bs * d * m * m
	# y is the audio feature: bs * d * nF
	# return: bs * n * m
	# print(x.size())
	bs = list(x.size())[0]
	D = x.size(1)
	assert(x.size(1)==y.size(1))
	x = x.contiguous().view(bs, D, -1) # bs * d * m^2
	x = x.div(torch.norm(x, p=2, dim=1, keepdim=True) + 1e-12)
	y = y.div(torch.norm(y, p=2, dim=1, keepdim=True) + 1e-12)
	cos_dis = torch.bmm(torch.transpose(x, 1, 2), y)#.transpose(1,2)
	cos_dis = 1 - cos_dis # to minimize this value
	# cos_dis = - cos_dis
	return cos_dis.transpose(2,1)


def cost_matrix_batch_torch_acos(x, y):
	"Returns the cosine distance batchwise"
	# x is the image feature: bs * d * m * m
	# y is the audio feature: bs * d * nF
	# return: bs * n * m
	# print(x.size())
	bs = list(x.size())[0]
	D = x.size(1)
	assert(x.size(1)==y.size(1))
	x = x.contiguous().view(bs, D, -1) # bs * d * m^2
	x = x.div(torch.norm(x, p=2, dim=1, keepdim=True) + 1e-12)
	y = y.div(torch.norm(y, p=2, dim=1, keepdim=True) + 1e-12)
	cos_dis = torch.bmm(torch.transpose(x,1,2), y)#.transpose(1,2)
	cos_dis = torch.acos(cos_dis) # to minimize this value
	# cos_dis = - cos_dis
	return cos_dis.transpose(2,1)

def cos_batch_torch(x, y, text_graph=False):
    "Returns the cosine distance batchwise"
    # x is the image feature: bs * d * m * m
    # y is the audio feature: bs * d * nF
    # return: bs * n * m
    # print(x.size())
    bs = x.size(0)
    D = x.size(1)
    assert(x.size(1)==y.size(1))
    x = x.contiguous().view(bs, D, -1) # bs * d * m^2
    x = x.div(torch.norm(x, p=2, dim=1, keepdim=True) + 1e-12)
    y = y.div(torch.norm(y, p=2, dim=1, keepdim=True) + 1e-12)
    cos_dis = torch.bmm(torch.transpose(x,1,2), y)#.transpose(1,2)
    cos_dis = 1 - cos_dis # to minimize this value
    # return cos_dis.transpose(2,1)
    if text_graph:
        return cos_dis
    # TODO:
    beta = 0.1
    min_score = cos_dis.min()
    max_score = cos_dis.max()
    threshold = min_score + beta * (max_score - min_score)
    res = cos_dis - threshold
    # res = torch.nn.ReLU()

    return torch.nn.functional.relu(res.transpose(2,1))


def pairwise_distances(x, y=None):
	'''
	Input: x is a Nxd matrix
		   y is an optional Mxd matirx
	Output: dist is a NxM matrix where dist[i,j] is the square norm between x[i,:] and y[j,:]
			if y is not given then use 'y=x'.
	i.e. dist[i,j] = ||x[i,:]-y[j,:]||^2
	'''
	x_norm = (x ** 2).sum(1).view(-1, 1)
	if y is not None:
		y_t = torch.transpose(y, 0, 1)
		y_norm = (y ** 2).sum(1).view(1, -1)
	else:
		y_t = torch.transpose(x, 0, 1)
		y_norm = x_norm.view(1, -1)

	dist = x_norm + y_norm - 2.0 * torch.mm(x, y_t)
	# Ensure diagonal is zero if x=y
	# if y is None:
	#     dist = dist - torch.diag(dist.diag)
	return torch.clamp(dist, 0.0, np.inf)

def row_pairwise_distances(x, y=None, dist_mat=None):
    if y is None:
        y = x
    if dist_mat is None:
        dtype = x.data.type()
        dist_mat = Variable(torch.Tensor(x.size()[0], y.size()[0]).type(dtype))

    for i, row in enumerate(x.split(1)):
        r_v = row.expand_as(y)
        sq_dist = torch.sum((r_v - y) ** 2, 1)
        dist_mat[i] = sq_dist.view(1, -1)
    return dist_mat

def IPOT_barycenter(p, C, q, iteration=20, beta=0.5, iteration_inner = 1):
	'''

	:param p: probability vector set, K x n
	:param C: cost matrix, K x n x n
	:param q: initial q, mean of all support, n x d
	:return:
	'''
	K = p.size(0)
	n = p.size(1)
	assert(C.size(1)==C.size(2))
	assert(C.size(1)==p.size(1))
	b = torch.ones(K, int(n), 1).cuda().detach()/float(n) # bs * m * 1
	C = torch.exp(-C/beta)
	T = torch.ones(K, n, n).cuda().detach().float()
	q = torch.unsqueeze(q, 0)
	for t in range(iteration):
		H = T * C
		for k in range(iteration_inner):
			a = q/torch.bmm(H, b)
			b = p/torch.bmm(torch.transpose(H, 2, 1), a)
			q = a * (torch.bmm(H, b))
		T = a * H * b.transpose(2,1)
	return q


def IPOT_distance_torch_batch_uniform(C, bs, n, m, iteration=50):
	C = C.float().cuda()
	T = IPOT_torch_batch_uniform(C, bs, n, m, iteration=iteration)
	temp = torch.bmm(torch.transpose(C,1,2), T)
	distance = batch_trace(temp, m, bs)
	return -distance

def IPOT_distance_torch_batch_uniform_T(C, bs, n, m, iteration=50):
	C = C.float().cuda()
	T = IPOT_torch_batch_uniform(C, bs, n, m, iteration=iteration)
	# temp = torch.bmm(torch.transpose(C,1,2), T)
	# distance = batch_trace(temp, m, bs)
	return T


def IPOT_torch_batch_uniform(C, bs, n, m, beta=0.5, iteration=50):
	# C is the distance matrix
	# c: bs by n by m
	sigma = torch.ones(bs, int(m), 1).cuda()/float(m)
	T = torch.ones(bs, n, m).cuda()
	A = torch.exp(-C/beta).float().cuda()
	for t in range(iteration):
		Q = A * T # bs * n * m
		for k in range(1):
			delta = 1 / (n * torch.bmm(Q, sigma))
			a = torch.bmm(torch.transpose(Q,1,2), delta)
			sigma = 1 / (float(m) * a)
		T = delta * Q * sigma.transpose(2,1)

	return T#.detach()


def GW_distance(X, Y, text_dep_graph, p, q, lamda=0.5, iteration=5, OT_iteration=20):
    '''
    :param X, Y: Source and target embeddings , batchsize by embed_dim by n
    :param p, q: probability vectors
    :param lamda: regularization
    :return: GW distance
    '''
    Cs = cos_batch_torch(X, X, True).float().cuda() * text_dep_graph
    Ct = cos_batch_torch(Y, Y).float().cuda()
    # pdb.set_trace()
    bs = Cs.size(0)
    m = Ct.size(2)
    n = Cs.size(2)
    T, Cst = GW_torch_batch(Cs, Ct, bs, n, m, p, q, beta=lamda, iteration=iteration, OT_iteration=OT_iteration)
    temp = torch.bmm(torch.transpose(Cst,1,2), T)
    distance = batch_trace(temp, m, bs)
    return distance

def GW_torch_batch(Cs, Ct, bs, n, m, p, q, beta=0.5, iteration=5, OT_iteration=20):
	one_m = torch.ones(bs, m, 1).float().cuda()
	one_n = torch.ones(bs, n, 1).float().cuda()

	Cst = torch.bmm(torch.bmm(Cs**2, p), torch.transpose(one_m, 1, 2)) + \
	      torch.bmm(one_n, torch.bmm(torch.transpose(q,1,2), torch.transpose(Ct**2, 1, 2))) # bs by n by m
	gamma = torch.bmm(p, q.transpose(2,1)) # outer product, init
	# gamma = torch.einsum('bi,bj->bij', (torch.squeeze(p), torch.squeeze(q))) # outer product, initialization
	for i in range(iteration):
		C_gamma = Cst - 2 * torch.bmm(torch.bmm(Cs, gamma), torch.transpose(Ct, 1, 2))
		# # Sinkhorn iteration
		# b = torch.ones(bs, m, 1).cuda()
		# K = torch.exp(-C_gamma/beta)
		# for i in range(50):cd
		# 	a = p/(torch.bmm(K, b))
		# 	b = q/torch.bmm(K.transpose(1,2), a)
		# gamma = a * K * b
		gamma = IPOT_torch_batch_uniform(C_gamma, bs, n, m, beta=beta, iteration=OT_iteration)
	Cgamma = Cst - 2 * torch.bmm(torch.bmm(Cs, gamma), torch.transpose(Ct, 1, 2))
	return gamma.detach(), Cgamma

# def GW_torch_batch(Cs, Ct, bs, n, m, beta=0.5, iteration=5, OT_iteration=20):
# 	one_m = torch.ones(bs, m, 1).float().cuda()
# 	one_n = torch.ones(bs, n, 1).float().cuda()
# 	p = (torch.ones(bs, m, 1)/m).cuda()
# 	q = (torch.ones(bs, n, 1)/n).cuda()

# 	Cst = torch.bmm(torch.bmm(Cs**2, p), torch.transpose(one_m, 1, 2)) + \
# 	      torch.bmm(one_n, torch.bmm(torch.transpose(q,1,2), torch.transpose(Ct**2, 1, 2))) # bs by n by m
# 	gamma = torch.bmm(p, q.transpose(2,1)) # outer product, init
# 	# gamma = torch.einsum('bi,bj->bij', (torch.squeeze(p), torch.squeeze(q))) # outer product, initialization
# 	for i in range(iteration):
# 		C_gamma = Cst - 2 * torch.bmm(torch.bmm(Cs, gamma), torch.transpose(Ct, 1, 2))
# 		gamma = IPOT_torch_batch_uniform(C_gamma, bs, n, m, beta=beta, iteration=OT_iteration)
# 	Cgamma = Cst - 2 * torch.bmm(torch.bmm(Cs, gamma), torch.transpose(Ct, 1, 2))
# 	return gamma.detach(), Cgamma

def GW_distance_uniform(X, Y, text_dep_graph, lamda=1e-1, iteration=5, OT_iteration=20):
	m = X.size(2)
	n = Y.size(2)
	bs = X.size(0)
	p = (torch.ones(bs, m, 1)/m).cuda()
	q = (torch.ones(bs, n, 1)/n).cuda()
	return GW_distance(X, Y, text_dep_graph, p, q, lamda=lamda, iteration=iteration, OT_iteration=OT_iteration)


def batch_diag(a_emb, n, bs):
	a = torch.eye(n).cuda().unsqueeze(0).repeat(bs, 1, 1) # bs * n * n
	b = (a_emb.unsqueeze(1).repeat(1,n,1))# bs * n * n
	return a*b
	# diagonal bs by n by n

def batch_trace(input_matrix, n, bs):
	a = torch.eye(n).cuda().unsqueeze(0).repeat(bs, 1, 1)
	b = a * input_matrix
	return torch.sum(torch.sum(b,-1),-1).unsqueeze(1)

In [ ]:
class GOTLoss(nn.Module):
    def __init__(self, **kwargs):
        super().__init__()
        self.args = kwargs
        self.got_lambda = self.args["got_lambda"]

    def GOT(self, v_, q_, text_dep_graph):
        cos_distance = cost_matrix_batch_torch(v_.transpose(2, 1), q_.transpose(2, 1))
        cos_distance = cos_distance.transpose(1,2)
        beta = 0.1
        min_score = cos_distance.min()
        max_score = cos_distance.max()
        threshold = min_score + beta * (max_score - min_score)
        cos_dist = torch.nn.functional.relu(cos_distance - threshold)

        wd = - IPOT_distance_torch_batch_uniform(cos_dist, v_.size(0), v_.size(1), q_.size(1), 30)
        gwd = GW_distance_uniform(v_.transpose(2,1), q_.transpose(2,1), text_dep_graph)
        twd = self.got_lambda * torch.mean(gwd) + (1 - self.got_lambda) * torch.mean(wd) # Temporarily commented: #self.args.got_lambda *

        return twd

    def forward(self, v_, q_):
        return self.GOT(v_, q_)

In [ ]:
def get_accuracy_and_avg_loss(model, processor, data_loader, device):
        # set model to eval
        model.eval()

        with torch.no_grad():
            tot_num_batches = 0
            tot_data = 0
            tot_batch_loss = 0
            tot_correct = 0

            for captions, images, adj_graphs, labels in tqdm(data_loader):

                model_inputs = processor(text=captions, images=images, return_tensors="pt", padding="max_length", max_length=77, return_codebook_pixels=True, return_image_mask=True).to(device)
                #print(model_inputs.attention_mask.shape)
                itm_labels = labels.to(device)
                text_dependency_graphs = adj_graphs.to(device)
                output = model(**model_inputs, itm_labels=itm_labels, text_dependency_graph=text_dependency_graphs)

                print(captions)
                print(output.loss_info.itm.item())
                print(output.loss_info.got.item())
                print(output.itm_logits)
                print(output.text_masked_embeddings)
                tot_correct += (output.itm_logits.argmax(dim=1) == itm_labels).sum().item()
                tot_batch_loss += output.loss_info.itm.item()
                tot_num_batches += 1
                tot_data += len(captions)
                print(tot_correct / tot_data)

        return tot_correct / tot_data, tot_batch_loss / tot_num_batches

In [ ]:
from transformers import FlavaProcessor, FlavaForPreTraining, FlavaModel

model = FlavaGOTForPreTraining.from_pretrained("model/run_5/epoch_0").to(device)
processor = FlavaProcessor.from_pretrained("facebook/flava-full")

In [ ]:
acc, loss = get_accuracy_and_avg_loss(model, processor, val_dataloader, device)

  0%|          | 0/596 [00:00<?, ?it/s]`input_ids_masked` isn't passed which means MLM loss won't be calculated correctlySetting it to `input_ids` so that model can work. Please pass it if this is unintentional. This is usually OKAY if you are doing inference on unmasked text...
/opt/conda/lib/python3.10/site-packages/transformers/modeling_utils.py:907: FutureWarning: The `device` argument is deprecated and will be removed in v5 of Transformers.
  warnings.warn(
  0%|          | 1/596 [00:00<09:52,  1.00it/s]

['A child holding a flowered umbrella and petting a yak.', 'A umbrella holding a flowered child and petting a yak.', 'A narrow kitchen filled with appliances and cooking utensils.', 'A narrow cooking filled with appliances and kitchen utensils.', 'A little girl holding a kitten next to a blue fence.', 'A blue girl holding a kitten next to a little fence.', 'A toilet sitting in a bathroom next to a sink.', 'A bathroom sitting in a toilet next to a sink.', 'There are two sinks next to two mirrors.', 'There are two mirrors next to two sinks.', 'A woman rides a bicycle on a road next to the median.', 'A bicycle rides a woman on a road next to the median.', 'A bath tub sitting next to a sink in a bathroom.', 'A sink tub sitting next to a bath in a bathroom.', 'A row of parked cars sitting next to parking meters.', 'A row of parked meters sitting next to parking cars.']
0.06378734111785889
0.001058154390193522
tensor([[-1.1067,  1.1886],
        [ 3.4258, -3.6875],
        [-0.9922,  1.0660]

`input_ids_masked` isn't passed which means MLM loss won't be calculated correctlySetting it to `input_ids` so that model can work. Please pass it if this is unintentional. This is usually OKAY if you are doing inference on unmasked text...
  0%|          | 2/596 [00:02<10:03,  1.02s/it]

['An elegant bathroom features a tub, sink, mirror, and decorations.', 'An elegant sink features a tub , bathroom , mirror , and decorations.', 'A red helmet is on a yellow toilet in the dirt.', 'A red toilet is on a yellow helmet in the dirt.', 'A car with some surfboards in a field.', 'A field with some surfboards in a car.', 'A cat on the lid of a toilet looking perturbed.', 'A lid on the cat of a toilet looking perturbed.', 'A woman is riding a motorcycle down the street.', 'A woman is riding a street down the motorcycle.', 'a person sitting at a desk with a keyboard and monitor', 'a desk sitting at a person with a keyboard and monitor', 'This is a case full of yellow bananas.', 'This is a case yellow of full bananas.', 'A small airplane taking off from an airport runway.', 'an airport runway taking off from a small airplane.']
0.15141232311725616
0.0013573942705988884
tensor([[-0.6282,  0.6745],
        [ 3.4842, -3.7503],
        [ 0.3328, -0.3615],
        [ 1.5829, -1.7072],
  

`input_ids_masked` isn't passed which means MLM loss won't be calculated correctlySetting it to `input_ids` so that model can work. Please pass it if this is unintentional. This is usually OKAY if you are doing inference on unmasked text...
  1%|          | 3/596 [00:02<09:04,  1.09it/s]

...

['A bathroom with a white bath tub under a window.', 'A bathroom with a white tub bath under a window.', 'A person holding a toothbrush under the running water of a faucet.', 'A person holding a toothbrush under the running faucet of a water.', 'A yellow book bus driving down a street.', 'A yellow street bus driving down a book.', 'A beautiful woman with red hair sitting at a table.', 'A red woman with beautiful hair sitting at a table.', 'A small white bird standing on top of a pond of water.', 'A small white bird standing on top of a water of pond.', 'A very dirty looking rest room with two toilets.', 'A very dirty rest looking room with two toilets.', 'A plate with chicken,carrots and mashed potatoes with silverware.', 'A chicken with plate , carrots and mashed potatoes with silverware.', 'A fork rests on a plate next to a piece of cake.', 'A fork rests on a piece next to a plate of cake.']
0.28985798358917236
0.0009216635371558368
tensor([[-2.0384,  2.1922],
        [ 1.1494, -1.24

`input_ids_masked` isn't passed which means MLM loss won't be calculated correctlySetting it to `input_ids` so that model can work. Please pass it if this is unintentional. This is usually OKAY if you are doing inference on unmasked text...
  3%|▎         | 17/596 [00:14<09:19,  1.03it/s]

['A crystal bowl filled with oranges on top of a table.', 'A crystal bowl filled with oranges on table of a top.', 'A silver motorcycle parked next to a forest filled with lots of trees.', 'A forest motorcycle parked next to a silver filled with lots of trees.', 'A man riding on the back of a motorcycle.', 'A back riding on the man of a motorcycle.', 'motorcycle bikes all parked next to each other lined up down the road.', 'road bikes all parked next to each other lined up down the motorcycle.', 'A large jetliner flying through a cloudy blue sky.', 'A large sky flying through a cloudy blue jetliner.', 'A humongous jumbo jet is on the airport runway.', 'A jumbo humongous jet is on the airport runway.', 'A small plan is parked half on a cement area and half in a field while the ground is wet.', 'A small plan is parked half on a cement area and half in a ground while the field is wet.', 'An airplane parked next to a terminal ready for passengers to board.', 'An terminal parked next to a a

  3%|▎         | 17/596 [00:15<08:46,  1.10it/s]


KeyboardInterrupt: 

In [ ]:
from accelerate import Accelerator


gradient_accumulation_steps=4
gradient_checkpointing=True
fp16=True

if gradient_checkpointing:
    model.gradient_checkpointing_enable()

optim = torch.optim.AdamW(model.parameters(), lr=2e-5, weight_decay=1e-2)

accelerator = Accelerator(cpu=False, mixed_precision='fp16')

model, optim, train_dataloader = accelerator.prepare(model, optim, train_dataloader)


Detected kernel version 4.14.327, which is below the recommended minimum of 5.5.0; this can cause the process to hang. It is recommended to upgrade the kernel to the minimum version or higher.


In [ ]:
acc, loss

(0.5071810462312611, 0.6930104615899986)

In [ ]:
epochs = 5

for epoch in range(1, epochs):
    with torch.autocast(device_type=device.type, dtype=torch.float16):
        i = 0
        for captions, images, adj_graphs, labels in tqdm(train_dataloader):
            model.train()
            model_inputs = processor(text=captions, images=images, return_tensors="pt", padding="max_length", max_length=77, return_codebook_pixels=True, return_image_mask=True).to(device)
            itm_labels = labels.to(device)
            text_dependency_graphs = adj_graphs.to(device)
            model_output = model(**model_inputs, itm_labels=itm_labels, text_dependency_graph=text_dependency_graphs)
            loss = model_output.loss
            print(loss, model_output.loss_info.itm)
            accelerator.backward(loss)
            optim.step()
            optim.zero_grad()
            i += 1

        model.save_pretrained(f"model/run_5/epoch_{epoch}")
        val_accuracy, val_loss = get_accuracy_and_avg_loss(model, processor, val_dataloader, device)
        with open(f"model/run_5/loss_epoch_{epoch}.pkl", "wb+") as f:
            pickle.dump(val_loss, f)
        with open(f"model/run_5/loss_accuracy_{epoch}.pkl", "wb+") as f:
            pickle.dump(val_accuracy, f)
        print(f"Val accuracy: {val_accuracy}, val loss: {val_loss}")

  0%|          | 0/13499 [00:00<?, ?it/s]`input_ids_masked` isn't passed which means MLM loss won't be calculated correctlySetting it to `input_ids` so that model can work. Please pass it if this is unintentional. This is usually OKAY if you are doing inference on unmasked text...


tensor(1.1890, device='cuda:0', grad_fn=<AddBackward0>) tensor(0.7191, device='cuda:0', grad_fn=<MulBackward0>)


  0%|          | 1/13499 [00:01<4:08:51,  1.11s/it]`input_ids_masked` isn't passed which means MLM loss won't be calculated correctlySetting it to `input_ids` so that model can work. Please pass it if this is unintentional. This is usually OKAY if you are doing inference on unmasked text...


tensor(1.0017, device='cuda:0', grad_fn=<AddBackward0>) tensor(0.6776, device='cuda:0', grad_fn=<MulBackward0>)


  0%|          | 2/13499 [00:02<3:57:46,  1.06s/it]`input_ids_masked` isn't passed which means MLM loss won't be calculated correctlySetting it to `input_ids` so that model can work. Please pass it if this is unintentional. This is usually OKAY if you are doing inference on unmasked text...


...

`input_ids_masked` isn't passed which means MLM loss won't be calculated correctlySetting it to `input_ids` so that model can work. Please pass it if this is unintentional. This is usually OKAY if you are doing inference on unmasked text...
 33%|███▎      | 198/596 [03:04<05:55,  1.12it/s]

['A very nice looking road and some bikes parked by the scooter.', 'a train with open doors at a terminal.', 'a terminal with open doors at a train.', 'A backpack next to a television and a gaming system.', 'A gaming next to a television and a backpack system.', 'A flying plane with smoke trailing behind it.', 'A trailing plane with smoke flying behind it.', 'Two giraffes on the grass in a fenced area.', 'Two giraffes on the area in a fenced grass.', 'The wing of an airplane over a large area with mountains.', 'The area of an airplane over a large wing with mountains.', 'A giraffe sticks his nose and tongue out of a wire fence to accept something a man is offering him.', 'A giraffe sticks his nose and tongue out of a man fence to accept something a wire is offering him.', 'A bent traffic light next to the side of a street.', 'A bent traffic side next to the light of a street.', 'People walking in the dirt where buses and vehicles are parked.']
0.10865828394889832
0.0009427033364772797


`input_ids_masked` isn't passed which means MLM loss won't be calculated correctlySetting it to `input_ids` so that model can work. Please pass it if this is unintentional. This is usually OKAY if you are doing inference on unmasked text...
 33%|███▎      | 199/596 [03:05<06:13,  1.06it/s]

['buses walking in the dirt where People and vehicles are parked.', 'A country road with a street light and signage', 'A country road with a signage light and street', 'a couple of giraffes walk next to a stone wall', 'a wall of giraffes walk next to a stone couple', 'A group of people that are behind a bus.', 'A bus of people that are behind a group.', 'A bench is surrounded by grass and a few flowers.', 'A grass is surrounded by bench and a few flowers.', 'A metal park bench sitting next to a small road.', 'a small road sitting next to a metal park bench.', 'A couple of goats and a goose in a green field moving about.', 'A couple of goats and a field in a green goose moving about.', 'A red fire hydrant sitting on the side of a road.', 'A hydrant fire red sitting on the side of a road.', 'Two very large birds pose outside on white chairs, side by side']
0.08496072888374329
0.0007988382130861282
tensor([[ 2.3516, -2.5312],
        [-0.4033,  0.4326],
        [ 1.1846, -1.2783],
       

`input_ids_masked` isn't passed which means MLM loss won't be calculated correctlySetting it to `input_ids` so that model can work. Please pass it if this is unintentional. This is usually OKAY if you are doing inference on unmasked text...
 34%|███▎      | 200/596 [03:06<06:19,  1.04it/s]

In [ ]:
torch.cuda.empty_cache()

In [ ]:
import sagemaker


s3_path_to_data = sagemaker.Session().upload_data(bucket='ebotta-storage',
                                                  path='model',
                                                  key_prefix='trained_model')
